In [1]:
import numpy as np
import pandas as pd

from net.modules import *
from net.decoder import *
from net.encoder import *

In [2]:
# Set up parameters (modify these as needed)
file_path = "data/bel_data_test.csv"  # Replace with your actual file path
encoder_type = "pca"  # Choose "regular" or "pca"
load_weights = False  # Set to True if you want to load pre-trained weights
weight_file = "weights/bel_weights.npz"  # Only used if load_weights is True
dataset="bel"

# Load and prepare the data
X_train, Y_train, X_test, Y_test = load_and_prepare_data(file_path)

In [3]:
# Set hyperparameters
input_size = X_train.shape[0]
hidden_size = 128
output_size = 61  # Number of classes
pca_components = 50

alpha = 0.01
iterations = 2000
num_trials = 5

In [4]:
# Choose encoder type
if encoder_type == "regular":
    EncoderClass = Encoder
    encoder_name = "Regular Encoder"
elif encoder_type == "pca":
    EncoderClass = PCAEncoder
    encoder_name = "PCAEncoder"
else:
    raise ValueError("Invalid encoder type selected")

In [5]:
# Load pre-trained weights or train a new model
if load_weights:
    encoder = EncoderClass(input_size, hidden_size, output_size, pca_components=pca_components)
    encoder.load_weights(weight_file)
    print(f"Weights loaded for {encoder_name}")
else:
    print(f"Training {encoder_name}")
    best_weights, best_accuracy, all_accuracies = best_params(
        EncoderClass, X_train, Y_train, input_size, hidden_size, output_size, 
        alpha, iterations, num_trials, pca_components=pca_components
    )
    print(f"Best accuracy achieved with {encoder_name}: {best_accuracy}")

    # Create encoder with best weights
    encoder = EncoderClass(input_size, hidden_size, output_size, pca_components=pca_components)
    encoder.W1, encoder.b1, encoder.W2, encoder.b2 = best_weights

    # Save the best weights
    weight_file = f"{dataset}_{encoder_name.lower().replace(' ', '_')}_weights.npz"
    encoder.save_weights(weight_file)
    print(f"Best weights saved to {weight_file}")


Training PCAEncoder
Trial 1/5


ValueError: X has 50 features, but StandardScaler is expecting 1024 features as input.

In [ ]:
# Initialize the appropriate Decoder
decoder = PCADecoder(encoder) if EncoderClass == PCAEncoder else Decoder(encoder)

In [ ]:
# Test the encoding-decoding process
num_test_images = 5
for i in range(num_test_images):
    original_image = X_test[:, i].reshape(input_size, 1)
    encoded = encoder.encode(original_image)
    reconstructed = decoder.decode(encoded)

    # Visualize the results
    img_dim = int(np.sqrt(input_size))
    plt.figure(figsize=(15, 5))
    
    plt.subplot(1, 3, 1)
    plt.imshow(original_image.reshape(img_dim, img_dim), cmap='gray')
    plt.title(f"Original Image {i+1}")
    
    plt.subplot(1, 3, 2)
    plt.imshow(encoded.reshape(output_size, 1), cmap='viridis', aspect='auto')
    plt.title(f"Encoded Image {i+1}")
    
    plt.subplot(1, 3, 3)
    plt.imshow(reconstructed.reshape(img_dim, img_dim), cmap='gray')
    plt.title(f"Reconstructed Image {i+1}")
    
    plt.tight_layout()
    plt.show()

    # Calculate and print the mean squared error
    mse = np.mean((original_image - reconstructed) ** 2)
    print(f"Mean Squared Error for Image {i+1}: {mse}")

print("Encoding-decoding process completed.")